![alt text](images/HDAT9500Banner.PNG)
<br>

# Chapter 6: Artificial Neural Networks / Deep Learning
# Assignment: Add regularization to a neural network by using Dropout

#####################################################################################

Double-click to write down your name and surname.

**Name:**
Alexander

**Surname:**
Kruskal

**Honour Pledge** <p>
    
    
Declaration: <p>
    
    
I declare that this assessment item is my own work, except where acknowledged, and has not been submitted for academic credit elsewhere or previously, or produced independently of this course (e.g. for a third party such as your place of employment) and acknowledge that the assessor of this item may, for the purpose of assessing this item: 

    a. Reproduce this assessment item and provide a copy to another member of the University; and/or 
    b. Communicate a copy of this assessment item to a plagiarism checking service (which may then retain a copy of the assessment item on its database for the purpose of future plagiarism checking). 

#####################################################################################

# 1. Introduction

In this exercise, we will regularize the deep neural network we built in the previous exercise.

"Dropout works by probabilistically removing, or “dropping out,” inputs to a layer, which may be input variables in the data sample or activations from a previous layer."

Read:

https://machinelearningmastery.com/how-to-reduce-overfitting-with-dropout-regularization-in-keras/
http://www.jmlr.org/papers/volume15/srivastava14a/srivastava14a.pdf

In particular, pay attention to the section: MLP Dropout Regularization.


## 1.1. Aims of the Exercise:

1. This is an introduction to Artificial Neural Networks / Deep Learning with regularization. 
2. We will use Keras.

 
It aligns with all of our course learning outcomes: 

1.	Distinguish a range of task specific machine learning techniques appropriate for Health Data Science.
2.	Design machine learning tasks for Health Data Science scenarios.
3.	Construct appropriate training and test sets for health research data.


## 1.2. Jupyter Notebook Intructions
1. Read the content of each cell.
2. Where necessary, follow the instructions that are written in each cell.
3. Run/Execute all the cells that contain Python code sequentially (one at a time), using the "Run" button.
4. For those cells in which you are asked to write some code, please write the Python code first and then execute/run the cell.
 
## 1.3. Tips
 1. The square brackets on the left hand side of each cell indicate whether the cell has been executed or not. Empty square brackets mean that the cell has not been executed, whereas square brackets that contain a number means that the cell has been executed. Run all the cells in sequence, using the "Run" button.
 2. To edit this notebook, just double-click in each cell. In the document, each cell can be a "Code" cell or "text-Markdown" cell. To choose between these two options, go to the combo-box above. 
 3. If you want to save your notebook, please make sure you press the "floppy disk" icon button above. 
 4. To clean the content of all cells and re-start the Notebook, please go to Cell->All Output->Clear

# 2. Load the Wisconsin Cancer Data Set and Prepare the data

For data dictionary and all information:
https://archive.ics.uci.edu/ml/datasets/Breast+Cancer+Wisconsin+(Diagnostic)

In [1]:
import sys
print(sys.version)
#For this notebook to work, Python must be 3.6.4 or 3.6.5

import numpy as np
import pandas as pd

3.6.4 |Anaconda, Inc.| (default, Jan 16 2018, 10:22:32) [MSC v.1900 64 bit (AMD64)]


In [2]:
cancer = pd.read_csv('data/breast-cancer-wisconsin-data/data.csv', sep=',')

# 3. Our first ANN using Keras


<div class="alert alert-block alert-success">**Start Activity**</div>

### <font color='blue'> Question 1: What is "dropout" in the context of ANNs? (5 marks) </font>

<b> Write answer here:</b>
#####################################################################################################################

Dropout randomly removes neurons from the forward pass and then updates are not applied to the dropped neurons on the backward pass.  
In practise, this prevents any one neuron from becoming too important and overfitting to the training dataset.  
This is believed to improve generalisation and prevent a deep learning network from becoming enrirely reliant on 1 or 2 nuerons.


#####################################################################################################################

### <font color='blue'> Question 2: Build the whole ANN as you did in the previous exercise. Add dropout regularization to the neural network. Choose an appropriate value for the regularization (tune the dropout value). Standardize the data. Make sure your experiments are reproducible. (65 marks) </font>

Seperate the data into training and test  
Create function to seperate and drop columns

In [3]:
def outcome_split(data_frame, column_names):
    """
    split dataframe between features and outcomes
    
    data_frames: dataframes
    column_names: string names in list (names after first index are just removed)
    
    return: dictionay with dropout rates as key and average accuracy score as values
    """
    
    outcome_df = data_frame[column_names[0]].values
    data_frame = data_frame.drop(columns= column_names, axis = 1)
    return (data_frame, outcome_df)

Drop 'id' and put 'diagnosis' into it's own category

In [4]:
X, y_categorical = outcome_split(cancer,['diagnosis', 'id'])

Label encode Y to binary  
**M = 1, B = 0**

In [5]:
# Encoding categorical data
from sklearn.preprocessing import LabelEncoder
labelencoder_X_1 = LabelEncoder()
y = labelencoder_X_1.fit_transform(y_categorical)

Split train and test data

In [6]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(X, y.ravel(), stratify=y, random_state=0, test_size = 0.30)

Import keras libraries

In [7]:
import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout, Activation
from keras.wrappers.scikit_learn import KerasClassifier
from keras.constraints import maxnorm

C:\Users\akrus\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
Using TensorFlow backend.


Set up StandarScaler and transform X_train and X_test for later

In [8]:
# Scaler/Standardization
from sklearn.preprocessing import StandardScaler
Scaler = StandardScaler()

#Scale train and test before forgetting
X_train_scaled = Scaler.fit_transform(X_train)
X_test_scaled = Scaler.transform(X_test)

Create grid search

In [9]:
import statistics
from sklearn.metrics import *


#set random seed
from numpy.random import seed
seed(4)
from tensorflow import set_random_seed
set_random_seed(9)


def gridsearch_param_ann(X,y):
    """
    gridsearch dropout rate parameters including average accuracy for 5 cross validations
    
    X: Training dataframe
    y: Training 
    
    return: data_frame with removed column_names, outcome_df
    """
    # dropout rates list
    dropout_rate = np.array([0.0,0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9])
    score_dict = {} #return dict
    
    
    #create 5 random splits ahead of time for grid search -random state is determined by i so it is reproducable
    list_train_valid =[] #list of lists
    for i in range(5):
        temp_list_valid = [] #reset
        X_train, X_valid, y_train, y_valid = train_test_split(X, y.ravel(), stratify=y, random_state=i, test_size = 0.20)
        #scale data
        X_train_scaled = Scaler.fit_transform(X_train)
        X_valid_scaled = Scaler.transform(X_valid)
        temp_list_valid = [X_train_scaled, y_train, X_valid_scaled, y_valid]
        list_train_valid.append(temp_list_valid)
                
    for j in range(len(dropout_rate)):
        dropout_rate1 = dropout_rate[j]
        dropout1 = str(dropout_rate[j])
        for k in range(len(dropout_rate)):
            dropout_rate2 = dropout_rate[k]
            dropout2 = str(dropout_rate[k])
            dropoutkey = 'ONE:' + dropout1 + '_TWO:' + dropout2
            
            #make model
            ann = Sequential()
            ann.add(Dense(output_dim = 16, kernel_initializer = 'uniform', input_dim = 30, activation =  'relu'))
            ann.add(Dropout(dropout_rate1))
            ann.add(Dense(output_dim = 16, kernel_initializer = 'uniform', activation = 'relu'))
            ann.add(Dropout(dropout_rate2))
            ann.add(Dense(output_dim=1, kernel_initializer='uniform', activation = 'sigmoid'))
            ann.compile(optimizer = 'adam',
                    loss = 'binary_crossentropy',
                    metrics = ['accuracy']
                    )
            accuracy_list = [] #list accuracy score for 5 fits with different splits test and valid
            for m in range(5): #different random splits each time but reproducable
                ann.fit(list_train_valid[m][0],list_train_valid[m][1], epochs=150, batch_size=100)
                #find accuracy
                y_pred = ann.predict_classes(list_train_valid[m][2])
                temp_accuracy_score = accuracy_score(list_train_valid[m][3], y_pred)
                accuracy_list.append(temp_accuracy_score)
                temp_average_acc = statistics.mean(accuracy_list)
            score_dict[dropoutkey]=temp_average_acc
            print(dropoutkey)
            print(accuracy_list)
            print(temp_average_acc)
                
    return(score_dict)

Run grid search

In [10]:
accuracy_scores = (gridsearch_param_ann(X_train, y_train))






Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


C:\Users\akrus\Anaconda3\lib\site-packages\ipykernel_launcher.py:47: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(kernel_initializer="uniform", input_dim=30, activation="relu", units=16)`
C:\Users\akrus\Anaconda3\lib\site-packages\ipykernel_launcher.py:49: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(kernel_initializer="uniform", activation="relu", units=16)`
C:\Users\akrus\Anaconda3\lib\site-packages\ipykernel_launcher.py:51: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(kernel_initializer="uniform", activation="sigmoid", units=1)`



Epoch 1/150
318/318 [==============================] - 0s 665us/step - loss: 0.6927 - acc: 0.6258
Epoch 2/150
318/318 [==============================] - 0s 19us/step - loss: 0.6911 - acc: 0.6698
Epoch 3/150
318/318 [==============================] - 0s 16us/step - loss: 0.6892 - acc: 0.6950
Epoch 4/150
318/318 [==============================] - 0s 16us/step - loss: 0.6865 - acc: 0.7358
Epoch 5/150
318/318 [==============================] - 0s 16us/step - loss: 0.6827 - acc: 0.8019
Epoch 6/150
318/318 [==============================] - 0s 38us/step - loss: 0.6774 - acc: 0.8365
Epoch 7/150
318/318 [==============================] - 0s 25us/step - loss: 0.6703 - acc: 0.8836
Epoch 8/150
318/318 [==============================] - 0s 28us/step - loss: 0.6610 - acc: 0.9119
Epoch 9/150
318/318 [==============================] - 0s 22us/step - loss: 0.6489 - acc: 0.9277
Epoch 10/150
318/318 [==============================] - 0s 41us/step - loss: 0.6333 - acc: 0.9308
Epoch 11/150
318/318 [=====

318/318 [==============================] - 0s 31us/step - loss: 0.0432 - acc: 0.9906
Epoch 83/150
318/318 [==============================] - 0s 25us/step - loss: 0.0428 - acc: 0.9906
Epoch 84/150
318/318 [==============================] - 0s 28us/step - loss: 0.0424 - acc: 0.9906
Epoch 85/150
318/318 [==============================] - 0s 38us/step - loss: 0.0421 - acc: 0.9906
Epoch 86/150
318/318 [==============================] - 0s 19us/step - loss: 0.0417 - acc: 0.9906
Epoch 87/150
318/318 [==============================] - 0s 25us/step - loss: 0.0411 - acc: 0.9906
Epoch 88/150
318/318 [==============================] - 0s 16us/step - loss: 0.0407 - acc: 0.9906
Epoch 89/150
318/318 [==============================] - 0s 34us/step - loss: 0.0402 - acc: 0.9906
Epoch 90/150
318/318 [==============================] - 0s 19us/step - loss: 0.0397 - acc: 0.9906
Epoch 91/150
318/318 [==============================] - 0s 31us/step - loss: 0.0393 - acc: 0.9906
Epoch 92/150
318/318 [===========

318/318 [==============================] - 0s 16us/step - loss: 0.0101 - acc: 1.0000
Epoch 16/150
318/318 [==============================] - 0s 25us/step - loss: 0.0101 - acc: 1.0000
Epoch 17/150
318/318 [==============================] - 0s 25us/step - loss: 0.0099 - acc: 1.0000
Epoch 18/150
318/318 [==============================] - 0s 34us/step - loss: 0.0098 - acc: 1.0000
Epoch 19/150
318/318 [==============================] - 0s 47us/step - loss: 0.0096 - acc: 1.0000
Epoch 20/150
318/318 [==============================] - 0s 47us/step - loss: 0.0094 - acc: 1.0000
Epoch 21/150
318/318 [==============================] - 0s 28us/step - loss: 0.0092 - acc: 1.0000
Epoch 22/150
318/318 [==============================] - 0s 25us/step - loss: 0.0090 - acc: 1.0000
Epoch 23/150
318/318 [==============================] - 0s 41us/step - loss: 0.0089 - acc: 1.0000
Epoch 24/150
318/318 [==============================] - 0s 44us/step - loss: 0.0088 - acc: 1.0000
Epoch 25/150
318/318 [===========

...

318/318 [==============================] - 0s 75us/step - loss: 0.4793 - acc: 0.7264
Epoch 85/150
318/318 [==============================] - 0s 78us/step - loss: 0.4785 - acc: 0.7390
Epoch 86/150
318/318 [==============================] - 0s 78us/step - loss: 0.4493 - acc: 0.7642
Epoch 87/150
318/318 [==============================] - 0s 78us/step - loss: 0.4503 - acc: 0.7642
Epoch 88/150
318/318 [==============================] - 0s 78us/step - loss: 0.4601 - acc: 0.7547
Epoch 89/150
318/318 [==============================] - 0s 75us/step - loss: 0.4461 - acc: 0.7673
Epoch 90/150
318/318 [==============================] - 0s 78us/step - loss: 0.4668 - acc: 0.7516
Epoch 91/150
318/318 [==============================] - 0s 69us/step - loss: 0.4449 - acc: 0.7421
Epoch 92/150
318/318 [==============================] - 0s 85us/step - loss: 0.4591 - acc: 0.7421
Epoch 93/150
318/318 [==============================] - 0s 82us/step - loss: 0.4489 - acc: 0.7862
Epoch 94/150
318/318 [===========

318/318 [==============================] - 0s 69us/step - loss: 0.4415 - acc: 0.7736
Epoch 17/150
318/318 [==============================] - 0s 78us/step - loss: 0.4772 - acc: 0.7390
Epoch 18/150
318/318 [==============================] - 0s 53us/step - loss: 0.4288 - acc: 0.7799
Epoch 19/150
318/318 [==============================] - 0s 63us/step - loss: 0.4626 - acc: 0.7421
Epoch 20/150
318/318 [==============================] - 0s 60us/step - loss: 0.4474 - acc: 0.7547
Epoch 21/150
318/318 [==============================] - 0s 56us/step - loss: 0.4640 - acc: 0.7421
Epoch 22/150
318/318 [==============================] - 0s 56us/step - loss: 0.4602 - acc: 0.7704
Epoch 23/150
318/318 [==============================] - 0s 56us/step - loss: 0.4735 - acc: 0.7547
Epoch 24/150
318/318 [==============================] - 0s 56us/step - loss: 0.4933 - acc: 0.7264
Epoch 25/150
318/318 [==============================] - 0s 56us/step - loss: 0.4591 - acc: 0.7516
Epoch 26/150
318/318 [===========

318/318 [==============================] - 0s 103us/step - loss: 0.4414 - acc: 0.7547
Epoch 100/150
318/318 [==============================] - 0s 94us/step - loss: 0.4599 - acc: 0.7642
Epoch 101/150
318/318 [==============================] - 0s 88us/step - loss: 0.4605 - acc: 0.7421
Epoch 102/150
318/318 [==============================] - 0s 82us/step - loss: 0.4570 - acc: 0.7704
Epoch 103/150
318/318 [==============================] - 0s 88us/step - loss: 0.4454 - acc: 0.7516
Epoch 104/150
318/318 [==============================] - 0s 75us/step - loss: 0.4753 - acc: 0.7358
Epoch 105/150
318/318 [==============================] - 0s 103us/step - loss: 0.4631 - acc: 0.7642
Epoch 106/150
318/318 [==============================] - 0s 85us/step - loss: 0.4507 - acc: 0.7610
Epoch 107/150
318/318 [==============================] - 0s 82us/step - loss: 0.4561 - acc: 0.7642
Epoch 108/150
318/318 [==============================] - 0s 91us/step - loss: 0.4645 - acc: 0.7453
Epoch 109/150
318/318 

318/318 [==============================] - 0s 78us/step - loss: 0.4633 - acc: 0.7358
Epoch 33/150
318/318 [==============================] - 0s 56us/step - loss: 0.4820 - acc: 0.7264
Epoch 34/150
318/318 [==============================] - 0s 82us/step - loss: 0.4461 - acc: 0.7673
Epoch 35/150
318/318 [==============================] - 0s 72us/step - loss: 0.4692 - acc: 0.7358
Epoch 36/150
318/318 [==============================] - 0s 72us/step - loss: 0.4575 - acc: 0.7516
Epoch 37/150
318/318 [==============================] - 0s 60us/step - loss: 0.3958 - acc: 0.8113
Epoch 38/150
318/318 [==============================] - 0s 56us/step - loss: 0.4423 - acc: 0.7799
Epoch 39/150
318/318 [==============================] - 0s 60us/step - loss: 0.4795 - acc: 0.7421
Epoch 40/150
318/318 [==============================] - 0s 75us/step - loss: 0.4689 - acc: 0.7547
Epoch 41/150
318/318 [==============================] - 0s 63us/step - loss: 0.4454 - acc: 0.7547
Epoch 42/150
318/318 [===========

318/318 [==============================] - 0s 63us/step - loss: 0.4583 - acc: 0.7484
Epoch 116/150
318/318 [==============================] - 0s 69us/step - loss: 0.4371 - acc: 0.7736
Epoch 117/150
318/318 [==============================] - 0s 66us/step - loss: 0.4870 - acc: 0.7610
Epoch 118/150
318/318 [==============================] - 0s 56us/step - loss: 0.4469 - acc: 0.7704
Epoch 119/150
318/318 [==============================] - 0s 60us/step - loss: 0.4395 - acc: 0.7767
Epoch 120/150
318/318 [==============================] - 0s 63us/step - loss: 0.4464 - acc: 0.7642
Epoch 121/150
318/318 [==============================] - 0s 75us/step - loss: 0.4308 - acc: 0.7736
Epoch 122/150
318/318 [==============================] - 0s 63us/step - loss: 0.4648 - acc: 0.7327
Epoch 123/150
318/318 [==============================] - 0s 63us/step - loss: 0.4459 - acc: 0.7610
Epoch 124/150
318/318 [==============================] - 0s 69us/step - loss: 0.4347 - acc: 0.7767
Epoch 125/150
318/318 [=

Look at 10 most and least accurate models

In [11]:
#Sort by key foward and back
best_sorted_accuracy_scores = sorted(accuracy_scores, key=accuracy_scores.get, reverse=True)
worst_sorted_accuracy_scores = sorted(accuracy_scores, key=accuracy_scores.get, reverse=False)

#Select key and values for best and worst
top10 = (best_sorted_accuracy_scores[:10])
last10 = (worst_sorted_accuracy_scores[:10])
best10 = ([accuracy_scores[x] for x in top10])
worst10 = ([accuracy_scores[x] for x in last10])

#print values with keys
print('Best Accuracy Scores:')
print(tuple(zip(top10, best10)))
print('Worst Accuracy Scores:')
print(tuple(zip(last10, worst10)))

Best Accuracy Scores:
(('ONE:0.4_TWO:0.6', 0.9925), ('ONE:0.6_TWO:0.9', 0.9925), ('ONE:0.0_TWO:0.9', 0.99), ('ONE:0.1_TWO:0.4', 0.99), ('ONE:0.1_TWO:0.7', 0.99), ('ONE:0.3_TWO:0.8', 0.99), ('ONE:0.3_TWO:0.9', 0.99), ('ONE:0.4_TWO:0.2', 0.99), ('ONE:0.4_TWO:0.3', 0.99), ('ONE:0.5_TWO:0.7', 0.99))
Worst Accuracy Scores:
(('ONE:0.7_TWO:0.2', 0.9775), ('ONE:0.9_TWO:0.2', 0.9775), ('ONE:0.0_TWO:0.4', 0.98), ('ONE:0.6_TWO:0.8', 0.98), ('ONE:0.7_TWO:0.1', 0.98), ('ONE:0.7_TWO:0.5', 0.98), ('ONE:0.7_TWO:0.7', 0.98), ('ONE:0.2_TWO:0.8', 0.9825), ('ONE:0.3_TWO:0.0', 0.9825), ('ONE:0.3_TWO:0.4', 0.9825))


### <font color='blue'> Question 3: Calculate accuracy, confusion matrix and all the metrics included in classification_report function. (15 marks) </font>

Reset random seeds  
Create model with best dropout rate parameters   
Fit model with Scaled data

In [12]:
#reset random seed
seed(4)
set_random_seed(9)

#make model with dropout rate of first =.3 and second = .6
ann = Sequential()
ann.add(Dense(output_dim = 16, kernel_initializer = 'uniform', input_dim = 30, activation =  'relu'))
ann.add(Dropout(.4))
ann.add(Dense(output_dim = 16, kernel_initializer = 'uniform', activation = 'relu'))
ann.add(Dropout(.6))
ann.add(Dense(output_dim=1, kernel_initializer='uniform', activation = 'sigmoid'))
ann.compile(optimizer = 'adam',
        loss = 'binary_crossentropy',
        metrics = ['accuracy']
        )

#fit model
ann.fit(X_train_scaled,y_train, epochs=150, batch_size=100)

C:\Users\akrus\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(kernel_initializer="uniform", input_dim=30, activation="relu", units=16)`
  import sys
C:\Users\akrus\Anaconda3\lib\site-packages\ipykernel_launcher.py:9: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(kernel_initializer="uniform", activation="relu", units=16)`
  if __name__ == '__main__':
C:\Users\akrus\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: UserWarning: Update your `Dense` call to the Keras 2 API: `Dense(kernel_initializer="uniform", activation="sigmoid", units=1)`
  # This is added back by InteractiveShellApp.init_path()


Epoch 1/150
398/398 [==============================] - 5s 12ms/step - loss: 0.6928 - acc: 0.6281
Epoch 2/150
398/398 [==============================] - 0s 68us/step - loss: 0.6914 - acc: 0.6633
Epoch 3/150
398/398 [==============================] - 0s 70us/step - loss: 0.6896 - acc: 0.6558
Epoch 4/150
398/398 [==============================] - 0s 70us/step - loss: 0.6876 - acc: 0.6734
Epoch 5/150
398/398 [==============================] - 0s 73us/step - loss: 0.6840 - acc: 0.6834
Epoch 6/150
398/398 [==============================] - 0s 90us/step - loss: 0.6804 - acc: 0.6985
Epoch 7/150
398/398 [==============================] - 0s 70us/step - loss: 0.6739 - acc: 0.7337
Epoch 8/150
398/398 [==============================] - 0s 85us/step - loss: 0.6651 - acc: 0.7412
Epoch 9/150
398/398 [==============================] - 0s 75us/step - loss: 0.6549 - acc: 0.7915
Epoch 10/150
398/398 [==============================] - 0s 93us/step - loss: 0.6417 - acc: 0.8216
Epoch 11/150
398/398 [=======

398/398 [==============================] - 0s 58us/step - loss: 0.0690 - acc: 0.9899
Epoch 85/150
398/398 [==============================] - 0s 58us/step - loss: 0.1012 - acc: 0.9774
Epoch 86/150
398/398 [==============================] - 0s 58us/step - loss: 0.0854 - acc: 0.9824
Epoch 87/150
398/398 [==============================] - 0s 50us/step - loss: 0.0716 - acc: 0.9849
Epoch 88/150
398/398 [==============================] - 0s 53us/step - loss: 0.0712 - acc: 0.9950
Epoch 89/150
398/398 [==============================] - 0s 55us/step - loss: 0.0854 - acc: 0.9925
Epoch 90/150
398/398 [==============================] - 0s 55us/step - loss: 0.0759 - acc: 0.9874
Epoch 91/150
398/398 [==============================] - 0s 60us/step - loss: 0.0680 - acc: 0.9849
Epoch 92/150
398/398 [==============================] - 0s 53us/step - loss: 0.0848 - acc: 0.9824
Epoch 93/150
398/398 [==============================] - 0s 53us/step - loss: 0.0774 - acc: 0.9899
Epoch 94/150
398/398 [===========

Get y-predicted based on test

In [13]:
y_pred = ann.predict_classes(X_test_scaled)

Make confusion matrix

In [14]:
# Making the Confusion Matrix
from sklearn.metrics import *

cm = confusion_matrix(y_true = y_test, y_pred = y_pred) #create confusion matrix

print('True positive = ', cm[0][0])
print('False positive = ', cm[0][1])
print('False negative = ', cm[1][0])
print('True negative = ', cm[1][1])

print("") #create space
print("Confusion matrix for best accuracy model:")
print(cm)


True positive =  99
False positive =  8
False negative =  3
True negative =  61

Confusion matrix for best accuracy model:
[[99  8]
 [ 3 61]]


**Scoring for the test:**  
Accuracy  
F1_macro  
ROC/AUC  
Classification Report

In [15]:
print("Accuracy on test set: {:.2f}".format(accuracy_score(y_test, y_pred)))
print("f1_macro on test set: {:.2f}".format(f1_score(y_test, y_pred, average = 'macro')))
print("ROC/AUC score on test set: {:.2f}".format(roc_auc_score(y_test, y_pred, average = 'macro')))
print('********************************')
print('Classification Report')
print('')
from sklearn.metrics import classification_report
print(classification_report(y_test, y_pred))

Accuracy on test set: 0.94
f1_macro on test set: 0.93
ROC/AUC score on test set: 0.94
********************************
Classification Report

             precision    recall  f1-score   support

          0       0.97      0.93      0.95       107
          1       0.88      0.95      0.92        64

avg / total       0.94      0.94      0.94       171



### <font color='blue'> Question 4: Write your conclusions about the performance and potential use of this classifier. Remember to refer to the original problem (step 0 - question) (15 marks) </font>

<b> Write answer here:</b>
#####################################################################################################################

My model has a drop out rate of .4 for the first hidden layer and .6 for the second hidden layer.  

Based on the performance of the model, I would be inclined to use the model to determine whether a person is likely to have cancer or not.
The accuracy is 94% which is extremely good, but more importantly, the precision for the negatives is 97%.
This means that there were very few false negatives; false negatives meaning that a person does have cancer but they innacurately are told they do not.
Further, a percision of 88% for the positives is a little high, but needing to do some extra testing to rule out a diagnosis is much less costly than missing someone who has cancer and is thought to not have it.

If I was to continue looking for better models, I would hopefully increace positive precision without decreasing negative precision.
  
Overall, the model is quite good and I would be comfortable using it as a guide, especially the model is more accurate than a doctor's ability.

#####################################################################################################################

<div class="alert alert-block alert-warning">**End Activity**</div>